[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://github.com/AlbertoGCID/Antiviral/blob/main/Antiviralautoencoder.ipynb)

condensacion de hart
6vs1

aplicar la extracción de características directamente a los previo de los smiles, sacar la fórmula, de la fórmula obtener una "imagen", una "matriz" para meterla dentro de una red convolucional, una vez está dentro de la red convolucional quitar la parte del clasificador (la salida del flatten) y esa salida será la selectora de características para aplicar las distintas técnicas de ML (la continuación del trabajo de Adriana pero con otro enfoque).

primero PCA o ANOVA

# Código extraído del trabajo de Adriana Anido Alonso
## https://github.com/adrania/COVID19-Drugs-repurposing/blob/main/Mordred_ML.ipynb

In [2]:
%matplotlib inline

import os
path = os.getcwd()
os.chdir(path)
import time
import pyqsar
import pickle
import numpy as np
import pandas as pd
from sklearn import metrics
import matplotlib.pyplot as plt

# Descriptors
from pandas import read_csv
from rdkit import Chem
from rdkit.Chem import Descriptors
from rdkit.ML.Descriptors import MoleculeDescriptors

#Processing
from sklearn.preprocessing import StandardScaler
from sklearn.feature_selection import VarianceThreshold, SelectKBest, mutual_info_classif
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV, StratifiedKFold

# Metrics
from sklearn.metrics import confusion_matrix, accuracy_score, roc_auc_score, f1_score, recall_score, precision_score, classification_report
from sklearn.utils import class_weight

# Machine learning
from sklearn.linear_model import LogisticRegression, SGDClassifier, RidgeClassifier
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis, QuadraticDiscriminantAnalysis
from sklearn.svm import SVC, LinearSVC, NuSVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier 
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, BaggingClassifier, AdaBoostClassifier, VotingClassifier, StackingClassifier, RandomTreesEmbedding
from sklearn.neural_network import MLPClassifier

In [3]:
def GetRdkitFeatures (descriptors, data):
    '''Gives a table of features from a smile. Descriptor's list is given by the user.'''

    calculator = MoleculeDescriptors.MolecularDescriptorCalculator(descriptors) # first it creates a calculator object with the descriptors
    #print(calculator.GetDescriptorSummaries()) # if we want to get a calculator summary
    values = [] # creates a list to append each value
    
    for smile in data.smiles:
        mol = Chem.MolFromSmiles(smile) # it creates a rdkit molecule object for each smile data
        if mol is None: continue
        desc = calculator.CalcDescriptors(mol) # generates a tuple with the features for each smile
        values.append(desc) # it accumulates each tuple in a list
        features = pd.DataFrame(values, columns = descriptors) # transform the list into a dataframe
    
    return features

def ProcessData(i):
    '''Replace not float values with NaN.'''
    try: 
        return float(i)
    except:
        return np.nan
    
def GetColumns (data):
    '''Gets those columns with a percentage of cells with NaN values >= 50%.'''
    columns = []
    for col in data:
        percent = data[col].isnull().sum()/data[col].isnull().count()
        if percent >= 0.5:
            columns.append(col)
    return columns

def ML_score (models, X_train, Y_train, X_test, Y_test, seed, classes = ['0','1']):
    '''Fit diferent models, predict and return models' scores'''
    ACC = 0
    AUROC = 0
    precision = 0 
    recall = 0
    f1score = 0
    
    model_name = type(models).__name__ # get model name
    start_time = time.time()
    
    # Train different models using cross validation 
    print('> Training time: %0.2f mins'% ((time.time()-start_time)/60))
        
    models.fit(X_train, Y_train)
    
    # Predict
    y_pred = models.predict(X_test)
    y_probs = models.predict_proba(X_test)[:, 1]
    model_report = classification_report(Y_test, y_pred, target_names=classes, output_dict=True, digits=3)
     
    # Scores
    ACC = accuracy_score(Y_test, y_pred)
    AUROC = roc_auc_score(Y_test, y_probs)
    precision = model_report['weighted avg']['precision']
    recall = model_report['weighted avg']['recall']
    f1score = model_report['weighted avg']['f1-score']
    
    return ACC, AUROC, precision, recall, f1score

In [3]:

# Load datasets
antiv = read_csv('antivirals_SMILES.csv')
drugs = read_csv('DB_SMILES4prediction.csv')

FileNotFoundError: [Errno 2] No such file or directory: 'antivirals_SMILES.csv'

In [ ]:

# Get RDKIT descriptors from smiles
des_list = [x[0] for x in Descriptors._descList] # get all rdkit posible descriptors

antiv_rdkit = pd.concat([antiv, GetRdkitFeatures(des_list, antiv)], axis=1)
drugs_rdkit = pd.concat([drugs, GetRdkitFeatures(des_list, drugs)], axis=1)

In [ ]:

# Save descriptors 
antiv_rdkit.to_csv('antiv_rdkit.csv', index_label=False)
drugs_rdkit.to_csv('drugs_rdkit.csv', index_label=False)

In [ ]:
# Load feature datasets
antiv_rdkit = read_csv('antiv_rdkit.csv', low_memory=False) #to solve different column types
antiv = antiv_rdkit.copy() # train

drugs_rdkit = read_csv('drugs_rdkit.csv', low_memory=False) #to solve different column types
drugs = drugs_rdkit.copy() # predict

In [ ]:
# Split ids and features
a = antiv.iloc[:,2:]
id_a = antiv.loc[:,:'Class']

d = drugs.iloc[:,3:]
id_d = drugs.loc[:,:'Class']

# Replace different column types with NaN values
a = a.applymap(ProcessData)
d = d.applymap(ProcessData)

# Restore datasets
antiv = pd.concat([id_a, a], axis=1)
drugs = pd.concat([id_d, d], axis=1)

In [ ]:
# First aproximation: any NaN value?
print('Has Antivirals dataset NaN values?', antiv.isnull().values.any()) #true
print('>> Columns with NaN: ', antiv.isnull().any().sum(), ' / ', len(antiv.columns))
print('>> Number of data points with NaN: ', antiv.isnull().any(axis=1).sum(), ' / ', len(antiv))
print('>> Number of rows with all NaN values: ', antiv.loc[:,'MaxEStateIndex':].isnull().all(axis=1).sum())

print('\nHas Drugs dataset NaN values?', drugs.isnull().values.any()) #true
print('>> Columns with NaN: ', drugs.isnull().any().sum(), ' / ', len(drugs.columns))
print('>> Number of data points with NaN: ', drugs.isnull().any(axis=1).sum(), ' / ', len(drugs))
print('>> Number of rows with all NaN values: ', drugs.loc[:,'MaxEStateIndex':].isnull().all(axis=1).sum())

In [ ]:
# Remove 8 rows with all NaN values in drugs dataset
all_NA = [10246,10247,10248,10249,10250,10251,10252,10253] # all nan values from 10246 till 10253
drugs = drugs.drop(all_NA) # remove 8 drugs from the drug dataset

In [ ]:

# Select columns to drop from antivirals dataset
to_drop = GetColumns(antiv)

# Drop the same columns in each dataset
antiv.drop(to_drop, axis=1, inplace=True) #same columns are removed
drugs.drop(to_drop, axis=1, inplace=True) #same columns are removed

In [ ]:
# Second aproximation 
print('Has Antivirals NaN values?', antiv.isnull().values.any()) #false
print('Has Drugs NaN values?', drugs.isnull().values.any()) #true

# Replace any NaN value with 0
antiv = antiv.fillna(0)
drugs = drugs.fillna(0)

print('Has Antivirals NaN values?', antiv.isnull().values.any()) #false
print('Has Drugs NaN values?', drugs.isnull().values.any()) #false

In [ ]:
# Save preprocessed files
antiv.to_csv('antiv_prepro_rdkit.csv', index_label=False)
drugs.to_csv('drugs_prepro_rdkit.csv', index_label=False)

In [201]:
# voy a probar a clasificar sin esto, ella usa media-varianza para la selección, así que le aplicaré media
# varianza también a los datos

def add_noise(df):
    noised_rows = []
    for i, row in df.iterrows():
        noised_row = row + np.random.normal(loc=0, scale=0.2, size=len(row))
        noised_row2 = row - np.random.normal(loc=0, scale=0.2, size=len(row))
        noised_rows.append(noised_row)
        noised_rows.append(noised_row2)
        noised_row = row + np.random.normal(loc=0, scale=0.2, size=len(row))
        noised_row2 = row - np.random.normal(loc=0, scale=0.2, size=len(row))
        noised_rows.append(noised_row)
        noised_rows.append(noised_row2)
    noised_df = pd.concat([df, pd.DataFrame(noised_rows, columns=df.columns)], ignore_index=True)
    return noised_df

def min_max_scaling(df):
    df_scaled = (df - df.min()) / (df.max() - df.min())
    df_scaled = df_scaled.where((df_scaled >= 0), 0)
    return df_scaled.where(~(df_scaled.eq(0).all(axis=0)), df_scaled + 1e-10)

def non_zero_mean_std(df):
    df = df.loc[:, (df != 0).any(axis=0)]
    df_scaled = (df-df.mean())/(df.std())
    return df_scaled

#df_train_se_aug= add_noise(df_train_se) - no aplico data augmentation

#df_train_se_stand = non_zero_mean_std(df_train_se) # estandarizo por mean_std eliminando columnas que son todo 0
#df_test_se_stand = non_zero_mean_std(df_test_se) 
#df_test_se_stand.head()

# Ejecutar siempre a partir de aquí

In [188]:
# Load dataset
input_data = read_csv('archivos/antiv_prepro_rdkit.csv')

In [189]:
# Remove smiles from dataset
input_data = input_data.loc[:,'Class':]

In [190]:
# Set categoricals
input_data['Class'] = pd.Categorical(input_data['Class'])

# Train and test dataset, one split 0.8 train, 0.2 test. Random_state=80
x = input_data[input_data.iloc[:,1:].columns] 
y = input_data['Class']

x_train, x_test, y_train, y_test = train_test_split(x.values, y.values, test_size=0.2, random_state=80)

print('Full dataset samples: {}'.format(input_data.shape[0]))
print('Train dataset samples: {}'.format(x_train.shape[0]))
print('Test dataset samples: {}'.format(x_test.shape[0]))

Full dataset samples: 229
Train dataset samples: 183
Test dataset samples: 46


In [191]:
# Standardize data using only train set
sc = StandardScaler().fit(x_train)
sc.get_params();

In [192]:
x_train_std = sc.transform(x_train)
x_test_std = sc.transform(x_test)

x_train_std.mean(axis=0);
x_train_std.std(axis=0);

In [193]:
# Transform splits from arrays into DataFrames

df_train = pd.DataFrame(x_train_std, columns=list(input_data.iloc[:,1:].columns))
df_train['Class'] = y_train

df_test = pd.DataFrame(x_test_std, columns=list(input_data.iloc[:,1:].columns))
df_test['Class'] = y_test

In [194]:
# FEATURE SELECTION - THRESHOLD
# Remove features with low variance - th=0.0001

dic_feats = dict()
for i in [1,0.001]:
    featFilter = VarianceThreshold(threshold=i) 
    X_high_variance_train = featFilter.fit_transform(x_train_std) # fit and transform train dataset
    selected_features = set(list(df_train.columns[featFilter.get_support(indices=True)])) # features with high variance
    print('Features with high variance: {}'.format(len(featFilter.get_support(indices=True)))) # how many with high variance
    pool_features = set(list(df_train.columns)[:-1]) # all features
    print('Total number of features: ', len(pool_features))
    eliminated_feats = list(pool_features-selected_features)[:-1] # eliminated features
    print('Eliminated features: ', len(eliminated_feats))
    X_high_variance_test = featFilter.transform(x_test_std) # transform test dataset
    dic_feats[i] = eliminated_feats

## aplicar laboratorio2 


Features with high variance: 88
Total number of features:  208
Eliminated features:  119
Features with high variance: 177
Total number of features:  208
Eliminated features:  30


In [195]:
# para elegir una de las columnas que voy a eliminar
varianza_nula = set(dic_feats[0.001])
varianza_minima = set(dic_feats[1])
candidatas_a_eliminar = list(varianza_minima - varianza_nula)
print(candidatas_a_eliminar[9])

BCUT2D_CHGLO


In [204]:
# para añadir una columna random al dataset
import random
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow import keras

def add_random_column(X_high_variance_train, X_high_variance_test,deleted_cols,
                                     df_train, df_test, num_cols,selected_features):
    # Check that both datasets have the same columns
    assert set(df_train.columns) == set(df_test.columns), "Train and test datasets have different columns"
    
    # Select random columns to be added
    random_cols = np.random.choice(list(deleted_cols), size=num_cols, replace=False)
    selected_features.update(random_cols)
    print(len(selected_features))
    # Add random columns to X_high_variance_train and X_high_variance_test
    for col in random_cols:
        idx = df_train.columns.get_loc(col)
        new_col_train = df_train.iloc[:, idx].values.reshape(-1, 1)
        X_high_variance_train = np.concatenate([X_high_variance_train, new_col_train], axis=1)
        
        idx = df_test.columns.get_loc(col)
        new_col_test = df_test.iloc[:, idx].values.reshape(-1, 1)
        X_high_variance_test = np.concatenate([X_high_variance_test, new_col_test], axis=1)
    
    return X_high_variance_train, X_high_variance_test,selected_features

def preparacion(X_high_variance_train,X_high_variance_test, varianza_nula, df_train,df_test,
                num_cols_added,selected_features,y_train,y_test):
    X_high_variance_train2,X_high_variance_test2,selected_features2 = add_random_column(X_high_variance_train,
                X_high_variance_test, varianza_nula, df_train,df_test,num_cols_added,selected_features)
    df_train_hv = pd.DataFrame(X_high_variance_train2, columns=selected_features2)
    df_train['Class'] = y_train
    df_test_hv = pd.DataFrame(X_high_variance_test2, columns=selected_features2)
    df_test['Class'] = y_test
    x_train,y_train,x_test,y_test = df_train_hv,y_train,df_test_hv,y_test
    x_train = x_train.values
    x_test = x_test.values
    y_train = y_train.to_numpy()
    y_test = y_test.to_numpy()
    return x_train,y_train,x_test,y_test

def entrenamiento(x_train,y_train,x_test,y_test,core1,core2,filtro1,filtro2):
    input_shape_x = (x_train.shape[1],)
    reshaped_input_shape = (1,12, 15)
    model = tf.keras.Sequential()
    model.add(tf.keras.layers.Reshape(target_shape=reshaped_input_shape, input_shape=input_shape_x))
    model.add(tf.keras.layers.Conv2D(filters=filtro1,kernel_size=(core1,core1),activation=tf.keras.activations.relu,padding="same"))     
    model.add(tf.keras.layers.Conv2D(filters=filtro2,kernel_size=(core2,core2),activation=tf.keras.activations.relu,padding="same"))
    model.add(tf.keras.layers.Flatten())
    model.add(tf.keras.layers.Dense(1, activation='sigmoid'))
    model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
    history = model.fit(x_train, y_train, epochs=500, batch_size=32, validation_data=(x_test, y_test))
    test_loss, test_acc = model.evaluate(x_test, y_test, verbose=0)
    y_pred = model.predict(x_test)
    y_pred_binary = np.round(y_pred)
    from sklearn.metrics import accuracy_score, roc_auc_score, precision_score, recall_score, f1_score
    acc = accuracy_score(y_test, y_pred_binary)
    auroc = roc_auc_score(y_test, y_pred)
    precision = precision_score(y_test, y_pred_binary)
    recall = recall_score(y_test, y_pred_binary)
    f1 = f1_score(y_test, y_pred_binary)
    return acc,auroc,precision,recall,f1

In [205]:
core1 = 3
core2 = 2
filtro1 = 32
filtro2 = 64
auroc_medio = list()
for i in range(5):
    x_train,y_train,x_test,y_test = preparacion(X_high_variance_train,X_high_variance_test, varianza_nula, df_train,df_test,
                3,selected_features,y_train,y_test)
    auroc_medio.append(entrenamiento(x_train,y_train,x_test,y_test,core1,core2,filtro1,filtro2)[1])
print(auroc_medio.sum()/5)

186


ValueError: Shape of passed values is (183, 180), indices imply (183, 186)

In [24]:
# Tested models (baseline)
models =  [LogisticRegression(random_state=seed, n_jobs=-1),
          LinearDiscriminantAnalysis(),
          QuadraticDiscriminantAnalysis(),
          
          DecisionTreeClassifier(random_state=seed),
                     
          SGDClassifier(loss='log',random_state=seed, n_jobs=-1),
          NuSVC(random_state=seed, probability=True),
          SVC(random_state=seed, probability=True),
          
          KNeighborsClassifier(n_jobs=-1),
          GaussianProcessClassifier(random_state=seed, n_jobs=-1),
          GaussianNB(),
          
          GradientBoostingClassifier(),
          BaggingClassifier(random_state=seed),
          AdaBoostClassifier(random_state=seed),
          RandomForestClassifier(n_jobs=-1, random_state=seed),
           
          MLPClassifier(random_state=seed),
          ]

In [25]:
# Create a dataframe for ML scores
df_ML = pd.DataFrame(columns=['Method', 'ACC', 'AUROC', 'Precision', 'Recall', 'F1-score'])

In [26]:
# Fit each model
for model in models:
    print("\n***", model)
    ACC, AUROC, precision, recall, f1score = ML_score(model, X_train, Y_train, X_test, Y_test, seed)
    df_ML = df_ML.append({'Method': str(type(model).__name__),
                          'ACC': float(ACC),
                          'AUROC': float(AUROC),
                          'Precision': float(precision),
                          'Recall': float(recall),
                          'F1-score': float(f1score)}, ignore_index=True)
df_ML


*** LogisticRegression(n_jobs=-1, random_state=42)
> Training time: 0.00 mins


/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/


*** LinearDiscriminantAnalysis()
> Training time: 0.00 mins

*** QuadraticDiscriminantAnalysis()
> Training time: 0.00 mins

*** DecisionTreeClassifier(random_state=42)
> Training time: 0.00 mins


/tmp/ipykernel_2062797/2978086970.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_ML = df_ML.append({'Method': str(type(model).__name__),
/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:173: FutureWarning: The loss 'log' was deprecated in v1.1 and will be removed in version 1.3. Use `loss='log_loss'` which is equivalent.
  warnings.warn(
/tmp/ipykernel_2062797/2978086970.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_ML = df_ML.append({'Method': str(type(model).__name__),
/tmp/ipykernel_2062797/2978086970.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_ML = df_ML.append({'Method': str(type(model).__name__),
/tmp/ipykernel_2062797/2978086970.py:5


*** SGDClassifier(loss='log', n_jobs=-1, random_state=42)
> Training time: 0.00 mins

*** NuSVC(probability=True, random_state=42)
> Training time: 0.00 mins

*** SVC(probability=True, random_state=42)
> Training time: 0.00 mins

*** KNeighborsClassifier(n_jobs=-1)
> Training time: 0.00 mins

*** GaussianProcessClassifier(n_jobs=-1, random_state=42)
> Training time: 0.00 mins


...


*** BaggingClassifier(random_state=42)
> Training time: 0.00 mins

*** AdaBoostClassifier(random_state=42)
> Training time: 0.00 mins


/tmp/ipykernel_2062797/2978086970.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_ML = df_ML.append({'Method': str(type(model).__name__),
/tmp/ipykernel_2062797/2978086970.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_ML = df_ML.append({'Method': str(type(model).__name__),



*** RandomForestClassifier(n_jobs=-1, random_state=42)
> Training time: 0.00 mins

*** MLPClassifier(random_state=42)
> Training time: 0.00 mins


/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:702: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/tmp/ipykernel_2062797/2978086970.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_ML = df_ML.append({'Method': str(type(model).__name__),


Method       ACC     AUROC  Precision    Recall  \
0              LogisticRegression  0.782609  0.761111   0.612476  0.782609   
1      LinearDiscriminantAnalysis  0.543478  0.591667   0.677847  0.543478   
2   QuadraticDiscriminantAnalysis  0.717391  0.783333   0.844472  0.717391   
3          DecisionTreeClassifier  0.782609  0.680556   0.782609  0.782609   
4                   SGDClassifier  0.760870  0.783333   0.808322  0.760870   
5                           NuSVC  0.891304  0.869444   0.895991  0.891304   
6                             SVC  0.869565  0.861111   0.863272  0.869565   
7            KNeighborsClassifier  0.847826  0.762500   0.842930  0.847826   
8       GaussianProcessClassifier  0.782609  0.755556   0.612476  0.782609   
9                      GaussianNB  0.739130  0.827778   0.823326  0.739130   
10     GradientBoostingClassifier  0.826087  0.863889   0.826087  0.826087   
11              BaggingClassifier  0.847826  0.779167   0.837554  0.847826   
12             AdaBoostClassifier  0.804348  0.761111   0.811745  0.804348   
13         RandomForestClassifier  0.869565  0.891667   0.869565  0.869565   
14                  MLPClassifier  0.804348  0.722222   0.843478  0.804348   

    F1-score  
0   0.687169  
1   0.583312  
2   0.742050  
3   0.782609  
4   0.775860  
5   0.893127  
6   0.864081  
7   0.844864  
8   0.687169  
9   0.760093  
10  0.826087  
11  0.837442  
12  0.807628  
13  0.869565  
14  0.735178

In [27]:

# Save results
df_ML.to_csv('Scores_rdkit.csv', index_label=False)

In [28]:

mlp = MLPClassifier(random_state=seed)

In [29]:
# GRIDSEARCH SELECTION
# GridSearchCV parameters
params = {
    'activation' : ['identity','logistic', 'tanh', 'relu'],
    'hidden_layer_sizes': [100, 150, 200],
    'learning_rate': ['constant', 'invscaling', 'adaptive'],
    'solver' : ['lbfgs', 'sgd', 'adam'],
    'beta_1': [0.5, 0.7, 0.9],
    'beta_2': [0.5, 0.7, 0.9],
    'epsilon':[0.00001, 0.0001, 0.001]
    
}

In [30]:
# GridSearch fit
gs = GridSearchCV(estimator=mlp, param_grid=params, verbose=10, scoring ='roc_auc', cv=3)

gs.fit(X_train, Y_train)

Fitting 3 folds for each of 2916 candidates, totalling 8748 fits
[CV 1/3; 1/2916] START activation=identity, beta_1=0.5, beta_2=0.5, epsilon=1e-05, hidden_layer_sizes=100, learning_rate=constant, solver=lbfgs


/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:559: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


[CV 1/3; 1/2916] END activation=identity, beta_1=0.5, beta_2=0.5, epsilon=1e-05, hidden_layer_sizes=100, learning_rate=constant, solver=lbfgs;, score=0.738 total time=   2.1s
[CV 2/3; 1/2916] START activation=identity, beta_1=0.5, beta_2=0.5, epsilon=1e-05, hidden_layer_sizes=100, learning_rate=constant, solver=lbfgs


/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:559: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


[CV 2/3; 1/2916] END activation=identity, beta_1=0.5, beta_2=0.5, epsilon=1e-05, hidden_layer_sizes=100, learning_rate=constant, solver=lbfgs;, score=0.794 total time=   1.8s
[CV 3/3; 1/2916] START activation=identity, beta_1=0.5, beta_2=0.5, epsilon=1e-05, hidden_layer_sizes=100, learning_rate=constant, solver=lbfgs


...

[CV 2/3; 2915/2916] END activation=relu, beta_1=0.9, beta_2=0.9, epsilon=0.001, hidden_layer_sizes=200, learning_rate=adaptive, solver=sgd;, score=0.556 total time=   0.5s
[CV 3/3; 2915/2916] START activation=relu, beta_1=0.9, beta_2=0.9, epsilon=0.001, hidden_layer_sizes=200, learning_rate=adaptive, solver=sgd


/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:702: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


[CV 3/3; 2915/2916] END activation=relu, beta_1=0.9, beta_2=0.9, epsilon=0.001, hidden_layer_sizes=200, learning_rate=adaptive, solver=sgd;, score=0.584 total time=   1.2s
[CV 1/3; 2916/2916] START activation=relu, beta_1=0.9, beta_2=0.9, epsilon=0.001, hidden_layer_sizes=200, learning_rate=adaptive, solver=adam
[CV 1/3; 2916/2916] END activation=relu, beta_1=0.9, beta_2=0.9, epsilon=0.001, hidden_layer_sizes=200, learning_rate=adaptive, solver=adam;, score=0.594 total time=   0.3s
[CV 2/3; 2916/2916] START activation=relu, beta_1=0.9, beta_2=0.9, epsilon=0.001, hidden_layer_sizes=200, learning_rate=adaptive, solver=adam
[CV 2/3; 2916/2916] END activation=relu, beta_1=0.9, beta_2=0.9, epsilon=0.001, hidden_layer_sizes=200, learning_rate=adaptive, solver=adam;, score=0.667 total time=   0.5s
[CV 3/3; 2916/2916] START activation=relu, beta_1=0.9, beta_2=0.9, epsilon=0.001, hidden_layer_sizes=200, learning_rate=adaptive, solver=adam
[CV 3/3; 2916/2916] END activation=relu, beta_1=0.9, bet

/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:559: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


GridSearchCV(cv=3, estimator=MLPClassifier(random_state=42),
             param_grid={'activation': ['identity', 'logistic', 'tanh', 'relu'],
                         'beta_1': [0.5, 0.7, 0.9], 'beta_2': [0.5, 0.7, 0.9],
                         'epsilon': [1e-05, 0.0001, 0.001],
                         'hidden_layer_sizes': [100, 150, 200],
                         'learning_rate': ['constant', 'invscaling',
                                           'adaptive'],
                         'solver': ['lbfgs', 'sgd', 'adam']},
             scoring='roc_auc', verbose=10)

In [31]:
best_params = gs.best_params_
print(best_params)

{'activation': 'tanh', 'beta_1': 0.5, 'beta_2': 0.5, 'epsilon': 1e-05, 'hidden_layer_sizes': 100, 'learning_rate': 'constant', 'solver': 'lbfgs'}


In [32]:
# Scores with GridSearch
ACC, AUROC, precision, recall, f1score = ML_score(gs.best_estimator_, X_train, Y_train, X_test, Y_test, seed)
print('ACC: ', ACC)
print('AUROC', AUROC)
print('Precision', precision)
print('Recall', recall)
print('F1Score', f1score)

> Training time: 0.00 mins
ACC:  0.6956521739130435
AUROC 0.8305555555555555
Precision 0.8093645484949833
Recall 0.6956521739130435
F1Score 0.7218326320710612


/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:559: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


In [33]:
# MANUAL SELECTION
mlp_best = MLPClassifier(random_state=seed, hidden_layer_sizes=49, beta_1=0.2, epsilon=0.00001)

ACC, AUROC, precision, recall, f1score = ML_score(mlp_best, X_train, Y_train, X_test, Y_test, seed)
print('ACC: ', ACC)
print('AUROC', AUROC)
print('Precision', precision)
print('Recall', recall)
print('F1Score', f1score)

> Training time: 0.00 mins
ACC:  0.782608695652174
AUROC 0.7416666666666667
Precision 0.6124763705103969
Recall 0.782608695652174
F1Score 0.687168610816543


/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:702: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/a1b3rt0/jupy/jup_notebook/lib/python3.10/site-packages/sklearn/metrics/_classi

In [34]:
# Save best model
model_rdkit = 'bestmodel_rdkit.sav'
pickle.dump(mlp_best, open(model_rdkit, 'wb'))

Para determinar cual de las técnicas aplicar, un punto esencial es determinar el tipo de variables de entrada y salida del problema que se está abordando. En el siguiente gráfico se puede ver la sugerencia segun estos tipos si son variables numéricas o bien categóricas.



Así en función del tipo de problema tendríamos:

* Entrada Numérica, Salida Numérica y correlación lineal: Método de Pearson ($R^2$). 
* Entrada Numérica, Salida Numérica y correlación NO lineal: Método de Spearman
### * Entrada Numérica, Salida Categórica y correlación lineal: ANOVA (Análisis de la varianza). 
### * Entrada Numérica, Salida Categórica y correlación NO lineal: Método de Kendall
* Entrada Categórica, Salida Numérica y correlación lineal: Método de Kendall 
* Entrada Categórica, Salida Numérica y correlación NO lineal: ANOVA (Análisis de la varianza)
* Entrada Categórica, Salida Numérica: $\chi^2$ ó Información Mutua

- Pearson’s Correlation Coefficient: [sklearn.feature_selection.f_regression()](https://scikit-learn.org/stable/modules/generated/sklearn.feature_selection.f_regression.html)
- Spearman’s rank correlation: [scipy.stats.spearmanr](https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.spearmanr.html)
- ANOVA: [sklearn.feature_selection.f_classif()](https://scikit-learn.org/stable/modules/generated/sklearn.feature_selection.f_classif.html)
- Kendall’s tau: [scipy.stats.kendalltau](https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.kendalltau.html)
- Chi-Squared: [sklearn.feature_selection.chi2()](https://scikit-learn.org/stable/modules/generated/sklearn.feature_selection.chi2.html)
- Mutual Information: [sklearn.feature_selection.mutual_info_classif](https://scikit-learn.org/stable/modules/generated/sklearn.feature_selection.mutual_info_classif.html) y [sklearn.feature_selection.mutual_info_regression()](https://scikit-learn.org/stable/modules/generated/sklearn.feature_selection.mutual_info_regression.html)

Para la selección se puede hacer uso de las funciones [sklearn.feature_selection.SelectKBest](https://scikit-learn.org/stable/modules/generated/sklearn.feature_selection.SelectKBest.html) y [sklearn.feature_selection.SelectPercentil](https://scikit-learn.org/stable/modules/generated/sklearn.feature_selection.SelectPercentile.html).Véase a continuación un ejemplo de aplicación.

## Nota: Ella usa información mútua, que es para entrada categórica y salida numérica, lo que habría que usar es Anova o Kendall